In [84]:
import numpy as np
import matplotlib.pyplot as plt

In [85]:
from loaders import clean_text_for_pattern_letter
from temp_text_puh import template_str
# input_str = clean_text_for_pattern_letter(template_str, out_len=len(template_str))
input_str = clean_text_for_pattern_letter(template_str, out_len=5000)
print(len(input_str))
letters = ['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u',
               'v', 'w', 'x', 'y', 'z', ' ', '.', ',', '"', '\'', '1']
print(f'{letters=}')

len(letters)=32
5000
letters=['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', ' ', '.', ',', '"', "'", '1']


In [86]:
def predict_train(input_str,
                  letters,
                  max_history=4,
                  max_index: int = 4,):
    WIN: dict[str, dict[str, int]] = {}

    HistoryHW: list[dict[str, int]] = []
    HistoryW: list[dict[str, dict[str, dict[int, int]]]] = []

    for h_idx in range(max_history):
        HistoryHW.append({})
        HistoryW.append({})

    IDX: list = []

    for letter in letters:
        WIN.setdefault(letter, {})

        for idx in range(max_index):
            WIN[letter].setdefault(idx, 0)

    prev_indices = [0]

    for inp_idx, inp in enumerate(input_str):
        if inp_idx <= 0:
            WIN[inp][prev_indices[0]] += 1
            continue

        IDX.append(prev_indices[0])

        IdxO = {}

        for h_idx in range(max_history):
            prev_idx = inp_idx - 1 - h_idx
            if prev_idx < 0:
                break

            prev_inp = input_str[prev_idx]

            HW = HistoryHW[h_idx]
            W = HistoryW[h_idx]

            key_HW = prev_inp + str(prev_indices[h_idx]) + ':' + inp

            if HW.get(key_HW, -1) != -1:
                inp_has_index = HW[key_HW]

                # idx_strength = W[prev_inp + str(prev_indices[h_idx])][inp][inp_has_index]

                IdxO.setdefault(inp_has_index, 0)
                IdxO[inp_has_index] += 1

        new_index = 0
        if len(IdxO) == 0:
            new_index = min(WIN[inp], key=WIN[inp].get)
        else:
            new_index = max(IdxO, key=IdxO.get)
        WIN[inp][new_index] += 1

        for h_idx in range(max_history):
            prev_idx = inp_idx - 1 - h_idx
            if prev_idx < 0:
                break

            prev_inp = input_str[prev_idx]

            key_I = prev_inp + str(prev_indices[h_idx])
            HistoryW[h_idx].setdefault(key_I, {})
            HistoryW[h_idx][key_I].setdefault(inp, {})
            HistoryW[h_idx][key_I][inp].setdefault(new_index, 0)
            HistoryW[h_idx][key_I][inp][new_index] += 1

            key_HW = prev_inp + str(prev_indices[h_idx]) + ':' + inp

            HistoryHW[h_idx].setdefault(key_HW, new_index)

        # recurtion
        prev_indices.insert(0, new_index)
        if len(prev_indices) > max_history:
            prev_indices = prev_indices[:-1]

    return HistoryW, HistoryHW, IDX

max_index_L1 = 32
max_history_L1 = 9

max_history_L1_ds = 11

HistoryW, HistoryHW, IDX = predict_train(input_str, letters, max_history=max_history_L1, max_index=max_index_L1)

for h_idx in range(max_history_L1):
    print(f'{h_idx=}')
    for wk, wv in HistoryW[h_idx].items():
        print(wk, wv)


h_idx=0
c0 {'h': {0: 1}}
h0 {'a': {0: 1}, 'e': {15: 1}}
a0 {'p': {0: 1}, 'l': {7: 1}, 'i': {15: 4}, 'n': {14: 4}, 'k': {8: 1}, 's': {0: 2}, 'b': {14: 1}}
p0 {'t': {0: 1}}
t0 {'e': {0: 1}, ' ': {14: 3}, 'h': {13: 1}}
e0 {'r': {0: 4}, ' ': {15: 5}, 'n': {2: 2}, 't': {2: 1, 18: 1}, 'c': {9: 1}, 'g': {16: 1}, 'i': {1: 1}}
r0 {' ': {0: 3}, 'h': {20: 1}, 'n': {31: 1}}
 0 {'i': {0: 2}, 'b': {7: 2}, 't': {19: 2}, 'w': {19: 2}, 'a': {30: 4, 15: 1}, 'h': {1: 3}, 's': {1: 1}, 'p': {30: 2}, 'l': {7: 1}}
i0 {'n': {0: 2}, 'm': {0: 2}, 's': {7: 2}, 'v': {6: 1}, 't': {11: 1, 12: 1}, 'l': {15: 1}, 'f': {27: 1}}
n0 {' ': {1: 1, 11: 2}, "'": {1: 1}, 'd': {11: 5}, 'n': {0: 1}, 'i': {20: 1}}
 1 {'w': {0: 2}, 'c': {5: 1}, 'o': {24: 1}, 's': {27: 1}, 'b': {11: 3}, 'i': {29: 1, 30: 1}, 'r': {19: 1}, 'y': {28: 1}}
w0 {'h': {1: 2}, 'i': {1: 1}, 'e': {8: 1}, 'a': {0: 1}}
h1 {'i': {1: 3}, 'r': {8: 1}, 'y': {7: 1}, 'o': {2: 1}}
i1 {'c': {1: 1}, 'n': {1: 3}, 'd': {2: 1}, 's': {20: 2, 0: 1}, ' ': {10: 1}}
c1 {'h': {

In [87]:
def to_probability(HistoryW: list[dict[str, dict[str, dict[int, int]]]], max_history: int):
    for h_idx in range(max_history):
        W = HistoryW[h_idx]

        for inp_symbol, s_indeces in W.items():
            symbol_stat_sum = 0

            for out_symbol, index_stat in s_indeces.items():
                for index, idx_stat in index_stat.items():
                    symbol_stat_sum += idx_stat

            for out_symbol, index_stat in s_indeces.items():
                for index, idx_stat in index_stat.items():
                    W[inp_symbol][out_symbol][index] = idx_stat / symbol_stat_sum
    
    return HistoryW
        
HistoryW = to_probability(HistoryW, max_history=max_history_L1)

for h_idx in range(max_history_L1):
    for wk, wv in HistoryW[h_idx].items():
        print(wk, wv)

c0 {'h': {0: 1.0}}
h0 {'a': {0: 0.5}, 'e': {15: 0.5}}
a0 {'p': {0: 0.07142857142857142}, 'l': {7: 0.07142857142857142}, 'i': {15: 0.2857142857142857}, 'n': {14: 0.2857142857142857}, 'k': {8: 0.07142857142857142}, 's': {0: 0.14285714285714285}, 'b': {14: 0.07142857142857142}}
p0 {'t': {0: 1.0}}
t0 {'e': {0: 0.2}, ' ': {14: 0.6}, 'h': {13: 0.2}}
e0 {'r': {0: 0.25}, ' ': {15: 0.3125}, 'n': {2: 0.125}, 't': {2: 0.0625, 18: 0.0625}, 'c': {9: 0.0625}, 'g': {16: 0.0625}, 'i': {1: 0.0625}}
r0 {' ': {0: 0.6}, 'h': {20: 0.2}, 'n': {31: 0.2}}
 0 {'i': {0: 0.1}, 'b': {7: 0.1}, 't': {19: 0.1}, 'w': {19: 0.1}, 'a': {30: 0.2, 15: 0.05}, 'h': {1: 0.15}, 's': {1: 0.05}, 'p': {30: 0.1}, 'l': {7: 0.05}}
i0 {'n': {0: 0.18181818181818182}, 'm': {0: 0.18181818181818182}, 's': {7: 0.18181818181818182}, 'v': {6: 0.09090909090909091}, 't': {11: 0.09090909090909091, 12: 0.09090909090909091}, 'l': {15: 0.09090909090909091}, 'f': {27: 0.09090909090909091}}
n0 {' ': {1: 0.09090909090909091, 11: 0.18181818181818182

In [88]:
def predict(input_str: str, 
            HistoryW: list[dict[str, dict[str, dict[int, int]]]], 
            max_history = 4,
            max_index = 4,):
    err = 0
    TF = []
    AL = []

    history_indices = []
    history_indices.append([x for x in range(max_index)])

    for input_idx, input in enumerate(input_str[:-1]):
        HO: dict[str, dict[int, int]] = {}
        HO_cnt: dict[str, dict[int, int]] = {}

        for h_idx in range(max_history):
            # print(f'{h_idx=}')

            inp_idx = input_idx - h_idx
            if inp_idx < 0:
                break
            # print(f'{h_idx=} {inp_idx=}')
            W = HistoryW[h_idx]
            inp = input_str[inp_idx]
            indices = history_indices[h_idx]

            key_I = inp + str(indices[0])
            O = W.get(key_I, {})
            # print(f'{O=}')
            # print()

            for index in indices[1:]:
                key_I = inp + str(index)

                index_O = W.get(key_I, {})
                # print(f'{index_O=}')
                # print()

                for key, val in index_O.items():
                    O.setdefault(key, {})
                    O[key].update(val)
            
            # print(f'{O=}')
            # print()
            
            for key_O, val_O in O.items():
                HO.setdefault(key_O, {})
                HO_cnt.setdefault(key_O, {})
                
                for key_index, val_index in val_O.items():
                    HO[key_O].setdefault(key_index, 0)
                    HO_cnt[key_O].setdefault(key_index, 0)

                    HO[key_O][key_index] += val_index
                    HO_cnt[key_O][key_index] += 1

        # print(f'{HO=}')
        # print(f'{HO_cnt=}')
        # print()

        length = 0
        for v in HO.values():
            length += len(v)

        max_arr = []
        for v in HO.values():
            col_max = max(v, key=v.get)
            max_arr.append(col_max)
        
        max_arr = np.array(max_arr)
        # tf = np.mean(np.abs(max_arr - max_arr[np.newaxis].T))

        tf = length
        # tf = len(HO)

        TF.append(tf)

        # max by cnt
        # max_symbol = 'a'
        # max_symbol_index = 0
        # max_val = 0
        # for key, val in HO_cnt.items():
        #     max_idx = max(val, key=val.get)
        #     # HO_cnt[key] = {max_idx: val[max_idx]}

        #     if val[max_idx] > max_val: # 
        #         max_val = val[max_idx]
        #         max_symbol_index = max_idx
        #         max_symbol = key
        # print(f'{max_symbol=}')
        # max by val
        max_symbol = 'a'
        max_symbol_index = 0
        max_val = 0
        # win_cnt = 0
        for key, val in HO.items():
            max_idx = max(val, key=val.get)
            HO[key] = {max_idx: val[max_idx]}

            # max_cnt = HO_cnt[key][max_idx]

            if val[max_idx] > max_val: # and max_cnt >= max_his:
                # print(f'{key=} {val[max_idx]=} {max_cnt=}')
                max_val = val[max_idx]
                max_symbol_index = max_idx
                max_symbol = key
                # win_cnt = max_cnt

        # print(f'{HO=}')
        next_inp = input_str[input_idx + 1]
        print(f'{max_symbol=}', f'{next_inp=} {max_val=} {HO=}', max_symbol_index, max_val)
        # print('')

        # anomaly
        if max_symbol == next_inp:
            AL.append(0)
        else:
            ni_v = HO.get(next_inp, 0)
            if ni_v == 0:
                AL.append(100)
            else:
                max_ni = max(ni_v, key=ni_v.get)
                AL.append(abs(ni_v[max_ni] - max_val))

        new_indices = [max_symbol_index]

        # err
        if max_symbol != next_inp:
            err += 1

            index_stats = HO.get(next_inp, 0)
            
            if index_stats == 0:
                new_indices = [x for x in range(max_index)]
                print(f'{new_indices=}')
            else:
                max_symbol_index = list(index_stats.keys())[0]

                new_indices = [max_symbol_index]
        
        # recurtion
        history_indices.insert(0, new_indices)
        if len(history_indices) > max_history:
            history_indices = history_indices[:-1]

    TF.append(0)
    AL.append(0)
    return err, TF, AL

err_L1, TF_L1, AL_L1 = predict(input_str, HistoryW, max_index=max_index_L1, max_history=max_history_L1)
# err_L1, TF_L1_no, AL_L1_no = predict(input_str, HistoryW, max_index=max_index_L1, max_history=max_history_L1)

print(err_L1, err_L1 / (len(input_str) / 100))

max_symbol='h' next_inp='h' max_val=1.0 HO={'h': {0: 1.0}, 'a': {15: 0.5}, 'e': {3: 1.0}, 'o': {20: 1.0}, 'k': {3: 1.0}, 'r': {11: 0.25}, 'i': {3: 0.125}, 'l': {31: 1.0}} 0 1.0
max_symbol='a' next_inp='a' max_val=1.5 HO={'a': {0: 1.5}, 'e': {15: 0.5}, ' ': {13: 1.0}, 'r': {8: 1.0}, 'm': {1: 1.0}, 'd': {1: 1.0}, 'u': {5: 1.0}, 'n': {1: 0.3333333333333333}, 'l': {26: 1.0}, 'i': {18: 1.0}, 'f': {15: 0.5}} 0 1.5
max_symbol='p' next_inp='p' max_val=1.5714285714285714 HO={'p': {0: 1.5714285714285714}, 'l': {5: 1.0}, 'i': {12: 1.0}, 'n': {14: 0.2857142857142857}, 'k': {8: 0.07142857142857142}, 's': {9: 0.5}, 'b': {19: 0.5}, ' ': {5: 1.0}, 'w': {1: 0.3333333333333333}, 'e': {21: 1.0}, 'o': {3: 0.3333333333333333}, "'": {1: 0.125}, 'c': {9: 0.25}, 'r': {3: 0.125}, 'u': {13: 0.5}, 't': {18: 0.25}, 'm': {25: 1.0}, 'y': {14: 1.0}, 'a': {20: 0.16666666666666666}, 'g': {14: 0.16666666666666666}, 'h': {26: 1.0}} 0 1.5714285714285714
max_symbol='t' next_inp='t' max_val=2.571428571428571 HO={'t': {0: 2

In [89]:
def get_word_stats(input_str: str | list, TF: list, threshold=0.0):
    buffer: list = [input_str[0]]
    WordStats: dict[str, int] = {}
    WordIndex: dict[str, int] = {}
    next_wrd_idx = 0

    NextLayerOut = []
    DownstreamIndex = {}

    prev_tf = TF[0]

    for inp_idx, inp in enumerate(input_str):
        if inp_idx <= 0 and inp_idx >= len(input_str) - 1:
            continue

        # if TF[inp_idx] - prev_tf > 0.0: # and abs(TF[inp_idx] - prev_tf) > 0.2:
        # and TF[inp_idx] > threshold:
        if TF[inp_idx] > prev_tf and TF[inp_idx] > TF[inp_idx + 1]:
            word = ''.join(buffer)

            WordStats.setdefault(word, 0)
            WordStats[word] += 1

            if not WordIndex.get(word):
                WordIndex.setdefault(word, next_wrd_idx)
                next_wrd_idx += 1

            wrd_idx = WordIndex.get(word)
            # NextLayerOut.append(str(wrd_idx))
            NextLayerOut.append(word)

            DownstreamIndex.setdefault(inp_idx, 1)

            buffer = [inp]
            prev_tf = TF[inp_idx]

            continue

        TF[inp_idx] = 0

        buffer.append(inp)
        prev_tf = TF[inp_idx]

    # sort
    WordStats = dict(sorted(WordStats.items(), key=lambda item: item[1], reverse=True))

    NextLayerOut.append(str(next_wrd_idx))
    return WordStats, WordIndex, NextLayerOut, DownstreamIndex


TF_L1 = np.array(TF_L1, dtype='float64')
AL_L1 = np.array(AL_L1, dtype='float64')
TF_L1 /= np.max(TF_L1)
AL_L1 /= np.max(AL_L1)
TF_L1 += AL_L1

TF_max_coef = 0.4

# TF_L1[np.where(TF_L1 < np.mean(TF_L1))] = 0
# TF_1 = TF_L1 - np.pad(TF_L1, (1, 0))[:-1]
# TF_2 = TF_L1 - np.pad(TF_L1, (0, 1))[1:]
# TF_L1 = TF_1 + TF_2

# TF_L1[np.where(TF_L1 < 0)] = 0
# TF_L1[np.where(TF_L1 < TF_max_coef)] = 0
TF_L1 = TF_L1.tolist()

WordStats_L1, WordIndex_L1, NextLayerOut_L1, DownstreamIndex_L1 = get_word_stats(input_str=input_str,
                                                                                 TF=TF_L1, 
                                                                                 threshold=0.0, )
print(len(WordStats_L1))
mean_WS = np.mean(np.array(list(WordStats_L1.values())))
print(f'{mean_WS=}')
WS_len = 0
for key, val in WordStats_L1.items():
    # if len(key.strip()) > 1 and val >= mean_WS:
    if val >= mean_WS:
        WS_len += 1
    print(key, val)
print(f'{WS_len=}')

print(f'{NextLayerOut_L1=}')
print(f'{len(NextLayerOut_L1)=}')

print(f'{WordIndex_L1=}')

print(f'{DownstreamIndex_L1=}')


786
mean_WS=2.1857506361323153
 a 43
 t 30
 b 23
 h 22
 w 22
 s 21
he 21
er 17
nd 15
ou 14
 r 14
 the 13
t  13
 i 13
 y 13
 he 12
 c 12
 of 11
 p 11
 th 11
ng 11
es 10
ing 10
 n 10
th 10
 f 10
id 10
 l 10
 o 10
om 9
d  9
 m 9
 to 9
an 9
ow 8
bu 8
in 8
as 8
or 8
is 8
sa 8
ed 8
ph 7
ly 7
ng  7
e  7
obin 7
the 6
 d 6
to 6
er  6
im 6
of 6
be 6
 i  6
aid 6
at 6
 g 6
y  6
ad 6
nd  6
ai 6
 be 5
ri 5
ns 5
 is 5
ay 5
hat 5
he  5
 po 5
ut 5
on 5
 sa 5
re 5
 so 5
o  5
s  5
ar 5
ie  4
it 4
 on 4
et 4
en 4
 it 4
 an 4
ea 4
nie 4
oh 4
 j 4
 do 4
ll 4
 e 4
sto 4
ike 4
r  4
 go 4
and 4
n  4
ho 4
ne 4
fu 4
oo 4
hi 3
ch 3
 wi 3
nn 3
nd t 3
ta 3
irs 3
 bu 3
ro 3
no 3
 if 3
hen 3
re  3
bo 3
 wh 3
ght 3
id  3
't 3
all 3
e's 3
ec 3
am 3
 in  3
 st 3
his 3
ab 3
pher 3
ha 3
co 3
 pooh 3
me 3
 wa 3
thi 3
zz 3
 a  3
 noise 3
ime 3
 and 3
 had 3
ing  3
we 3
ni 3
ra 3
 ba 3
 in 2
ome 2
n h 2
mp  2
bin  2
 kn 2
 fe 2
lly 2
ny 2
tt 2
od 2
 yo 2
 goi 2
as a 2
win 2
po 2
 mea 2
e i 2
get 2
nnie 2
oh l 2
ikes 2
ort 2


In [90]:
def downstream_train(input: list, next_layer_out: list, downstream_index: dict[int, int]):
    DSStats = {}

    ds_idx = 1
    ds_inp = next_layer_out[0]

    for inp_idx, inp in enumerate(input[:-1]):
        has_ds_input = downstream_index.get(inp_idx)
        if has_ds_input:
            ds_inp = next_layer_out[ds_idx]
            ds_idx += 1

        ds_key = ds_inp + ':' + inp
        DSStats.setdefault(ds_key, 0)
        DSStats[ds_key] += 1

    return DSStats


DSStats = downstream_train(input=input_str,
                           next_layer_out=NextLayerOut_L1,
                           downstream_index=DownstreamIndex_L1,)

for wk, wv in DSStats.items():
    print(wk, wv)

ccha:c 1
ccha:h 1
ccha:a 1
pter :p 1
pter :t 1
pter :e 1
pter :r 1
pter :  1
in w:i 1
in w:n 1
in w:  1
in w:w 1
hi:h 3
hi:i 3
ch:c 3
ch:h 3
 we are:  2
 we are:w 1
 we are:e 2
 we are:a 1
 we are:r 1
 in:  2
 in:i 2
 in:n 2
trod:t 1
trod:r 1
trod:o 1
trod:d 1
uce:u 1
uce:c 1
uce:e 1
d to:d 1
d to:  1
d to:t 1
d to:o 1
 wi:  3
 wi:w 3
 wi:i 3
nn:n 6
ie :i 4
ie :e 4
ie :  4
the:t 6
the:h 6
the:e 6
 poo:  1
 poo:p 1
 poo:o 2
h a:h 1
h a:  1
h a:a 1
nd:n 15
nd:d 15
 s:  21
 s:s 21
ome:o 2
ome:m 2
ome:e 2
 be:  5
 be:b 5
 be:e 5
es:e 10
es:s 10
 a:  43
 a:a 43
nd t:n 3
nd t:d 3
nd t:  3
nd t:t 3
he:h 21
he:e 21
 sto:  1
 sto:s 1
 sto:t 1
 sto:o 1
ri:r 5
ri:i 5
gi:g 1
gi:i 1
n h:n 2
n h:  2
n h:h 2
er:e 17
er:r 17
e is ed:e 2
e is ed:  2
e is ed:i 1
e is ed:s 1
e is ed:d 1
wa:w 1
wa:a 1
rd:r 1
rd:d 1
 bear c:  2
 bear c:b 1
 bear c:e 1
 bear c:a 1
 bear c:r 1
 bear c:c 1
om:o 9
om:m 9
ing:i 10
ing:n 10
ing:g 10
 d:  6
 d:d 6
ow:o 8
ow:w 8
ns:n 5
ns:s 5
ta:t 3
ta:a 3
irs:i 3
irs:r 3
irs:s 3


In [91]:
def downstream_predict(input_str: str, 
            HistoryW: list[dict[str, dict[str, dict[int, int]]]], 
            upstream_inp: dict[int, list],
            DSStats: dict[str, int],
            ds_input: list,
            max_history = 4,
            max_index = 4,):
    err = 0
    TF = []

    history_indices = []
    history_indices.append([x for x in range(max_index)])

    ds_idx = 1
    ds_inp = ds_input[0]

    for input_idx, input in enumerate(input_str[:-1]):
        HO: dict[str, dict[int, int]] = {}

        for h_idx in range(max_history):
            inp_idx = input_idx - h_idx
            if inp_idx < 0:
                break
            # print(f'{h_idx=} {inp_idx=}')
            W = HistoryW[h_idx]
            inp = input_str[inp_idx]
            indices = history_indices[h_idx]

            key_I = inp + str(indices[0])
            # print(f'{key_I=}')
            O = W.get(key_I, {})
            # print(f'{O=}')
            # print()

            for index in indices[1:]:
                key_I = inp + str(index)
                # print(f'{key_I=}')

                index_O = W.get(key_I, {})
                # print(f'{index_O=}')
                # print()

                for key, val in index_O.items():
                    O.setdefault(key, {})
                    O[key].update(val)
            
            # print(f'{O=}')
            # print()
            
            for key_O, val_O in O.items():
                HO.setdefault(key_O, {})
                
                for key_index, val_index in val_O.items():
                    HO[key_O].setdefault(key_index, 0)

                    HO[key_O][key_index] += val_index

        # print(f'{HO=}')
        # print()

        length = 0
        for v in HO.values():
            length += len(v)

        # tf = length
        tf = len(HO)

        TF.append(tf)

        # ds input
        has_ds_input = upstream_inp.get(input_idx + 1)
        if has_ds_input:
            ds_inp = ds_input[ds_idx]
            ds_idx += 1

        # max symbol
        max_symbol = 'a'
        max_symbol_index = 0
        max_val = 0
        for key, val in HO.items():
            max_idx = max(val, key=val.get)
            HO[key] = {max_idx: val[max_idx]}
            max_idx_val = val[max_idx]

            # ds predict
            ds_key = ds_inp + ':' + key
            ds_stats = DSStats.get(ds_key)
            # if ds_stats:
            #     max_idx_val += ds_stats

            if max_idx_val > max_val and ds_stats:
                max_val = max_idx_val
                max_symbol_index = max_idx
                max_symbol = key

        # print(f'{HO=}')
        next_inp = input_str[input_idx + 1]
        print(f'{max_symbol=}', f'{next_inp=} {ds_inp=} {HO=}', max_symbol_index, max_val)

        # print(f'{O.get(max_symbol).keys()=}')
        new_indices = [max_symbol_index]

        if O.get(max_symbol):
            new_indices = list(O.get(max_symbol).keys())            

        # err
        if max_symbol != next_inp:
            err += 1

            index_stats = HO.get(next_inp, 0)
            
            if index_stats == 0:
                new_indices = [x for x in range(max_index)]
                print(f'{new_indices=}')
            else:
                max_symbol_index = list(index_stats.keys())[0]

                new_indices = [max_symbol_index]
        
        # recurtion
        history_indices.insert(0, new_indices)
        if len(history_indices) > max_history:
            history_indices = history_indices[:-1]

    return err, TF

HistoryW, HistoryHW, IDX = predict_train(input_str, letters, max_history=max_history_L1_ds, max_index=max_index_L1)

# for h_idx in range(max_history_L1_ds):
#     print(f'{h_idx=}')
#     for wk, wv in HistoryW[h_idx].items():
#         print(wk, wv)

err_L1_ds, TF_L1_ds = downstream_predict(input_str=input_str, 
                                        HistoryW=HistoryW, 
                                        upstream_inp=DownstreamIndex_L1,
                                        DSStats=DSStats,
                                        ds_input=NextLayerOut_L1,
                                        max_history=max_history_L1_ds,
                                        max_index=max_index_L1, )

print(f'{err_L1=}', err_L1 / (len(input_str) / 100))
print(f'{err_L1_ds=}', err_L1_ds / (len(input_str) / 100))

max_symbol='h' next_inp='h' ds_inp='ccha' HO={'h': {29: 4}, 'e': {4: 3}, 'a': {27: 2}, 'o': {15: 4}, 'k': {4: 3}, 'r': {30: 1}, 'l': {4: 3}, 'i': {22: 1}} 29 4
max_symbol='a' next_inp='a' ds_inp='ccha' HO={'a': {5: 9}, 'o': {2: 3}, 'e': {16: 30}, ' ': {13: 3}, 'i': {9: 5}, 't': {8: 3}, 'r': {26: 9}, 'y': {25: 1}, 'd': {1: 1}, 'n': {24: 1}, 'm': {5: 3}, 'u': {14: 2}, 'l': {9: 3}, 'f': {0: 1}} 5 9
max_symbol='t' next_inp='p' ds_inp='pter ' HO={'p': {0: 4}, 't': {24: 10}, 'i': {2: 4}, 'n': {15: 7}, 'c': {6: 2}, 's': {31: 10}, 'h': {29: 2}, 'u': {15: 1}, ' ': {10: 7}, 'w': {8: 3}, 'l': {10: 3}, "'": {2: 1}, 'y': {19: 2}, 'd': {13: 3}, 'r': {25: 10}, 'a': {1: 2}, 'v': {0: 1}, 'b': {21: 2}, 'e': {13: 1}, 'o': {15: 2}, 'm': {0: 4}, 'g': {9: 1}} 24 10
max_symbol=' ' next_inp='t' ds_inp='pter ' HO={'t': {0: 4}, 'e': {11: 6}, 'i': {3: 1}, 'd': {13: 4}, ' ': {10: 18}, 'k': {8: 3}, 'h': {29: 5}, 's': {14: 9}, 'l': {17: 7}, 'b': {0: 4}, 'c': {13: 2}, 'g': {2: 4}, 'o': {4: 3}, 'w': {8: 3}, 'r': {25: